In [2]:
import numpy as np
import matplotlib.pyplot as plt
from itertools import product
from timeit import default_timer as timer
import gurobipy as gp
import statistics
import scipy.stats as stats
from gurobipy import Model, GRB, quicksum

# Inicialización de constantes


In [3]:
T = np.zeros((12,3)) # T es estocástico porque depende de alpha.
W = np.zeros((12,21))
for i in range(0,12):
    W[i,i] = 1
    if( i < 9 ):
        W[i,i+12] = 1
        W[9+i%3,i] = 1
q = np.append(np.append(np.full(9,7),np.full(3,30)),np.zeros(9))
print(q)
c = np.array([10,15,20])

A = np.array([[0,0,0]])
b = np.array([0])

[ 7.  7.  7.  7.  7.  7.  7.  7.  7. 30. 30. 30.  0.  0.  0.  0.  0.  0.
  0.  0.  0.]


In [ ]:
alposibles = [(0.2761102779082043, 0.707532448596497, 0.09752767573882204), (0.2761102779082043, 0.707532448596497, 0.04921506030880329), 
                        (0.2761102779082043, 0.707532448596497, 0.37569966579172187), (0.2761102779082043, 0.707532448596497, 0.4701189332667809), 
                        (0.2761102779082043, 0.707532448596497, 0.5385808734778176), (0.2761102779082043, 0.647831685172105, 0.20750979334908126), 
                        (0.2761102779082043, 0.647831685172105, 0.5997119607126357), (0.2761102779082043, 0.647831685172105, 0.3613733970402435), 
                        (0.2761102779082043, 0.647831685172105, 0.8340704810711529), (0.2761102779082043, 0.647831685172105, 0.3695524799572454), 
                        (0.4214693794312172, 0.021861850414628292, 0.17546654843610343), (0.4214693794312172, 0.021861850414628292, 0.1219463901922131), 
                        (0.4214693794312172, 0.021861850414628292, 0.5759763514808928), (0.4214693794312172, 0.021861850414628292, 0.49079512529101943), 
                        (0.4214693794312172, 0.021861850414628292, 0.4444567881570156), (0.4214693794312172, 0.9619471387099465, 0.7643259261950858), 
                        (0.4214693794312172, 0.9619471387099465, 0.16871855643550915), (0.4214693794312172, 0.9619471387099465, 0.9486575901113345), 
                        (0.4214693794312172, 0.9619471387099465, 0.4717851274873406), (0.4214693794312172, 0.9619471387099465, 0.7886644127901323), 
                        (0.5989582847945334, 0.5503144816475992, 0.769083831826168), (0.5989582847945334, 0.5503144816475992, 0.6310081923701275), (0.5989582847945334, 0.5503144816475992, 0.5309577622884225), (0.5989582847945334, 0.5503144816475992, 0.941937070863148), (0.5989582847945334, 0.5503144816475992, 0.8836129321310429), (0.5989582847945334, 0.5347181514045396, 0.9027929908972264), (0.5989582847945334, 0.5347181514045396, 0.6330653067631413), (0.5989582847945334, 0.5347181514045396, 0.5574263726583272), 
                        (0.5989582847945334, 0.5347181514045396, 0.0851410172259488), (0.5989582847945334, 0.5347181514045396, 0.7131612487592662), (0.10843420381075952, 0.5945066309361564, 0.7474921039636828), (0.10843420381075952, 0.5945066309361564, 0.17949879727846718), (0.10843420381075952, 0.5945066309361564, 0.8172110624718085), (0.10843420381075952, 0.5945066309361564, 0.423154893061903), (0.10843420381075952, 0.5945066309361564, 0.2696042566022563), (0.10843420381075952, 0.9190360863265952, 0.9767390799587229), (0.10843420381075952, 0.9190360863265952, 0.9097956727953114), (0.10843420381075952, 0.9190360863265952, 0.5196202458505507), (0.10843420381075952, 0.9190360863265952, 0.9682096743104093), 
                        (0.10843420381075952, 0.9190360863265952, 0.2044072727896057), (0.6315017683628069, 0.02395578097993112, 0.34384611150502886), (0.6315017683628069, 0.02395578097993112, 0.3290035265783212), (0.6315017683628069, 0.02395578097993112, 0.09813842654451943), (0.6315017683628069, 0.02395578097993112, 0.7370545337643982), (0.6315017683628069, 0.02395578097993112, 0.2824462989095523), (0.6315017683628069, 0.13870147891765483, 0.2109691323490409), (0.6315017683628069, 0.13870147891765483, 0.08419044213233651), (0.6315017683628069, 0.13870147891765483, 0.2282421331409733), (0.6315017683628069, 0.13870147891765483, 0.11811468862298302), (0.6315017683628069, 0.13870147891765483, 0.8725250106511109)]

dposibles =[(21, 226, 370), (21, 226, 419), (21, 226, 273), (21, 226, 458), (21, 226, 499), (21, 92, 435), 
            (21, 92, 386), (21, 92, 320), (21, 92, 285), (21, 92, 282), (72, 177, 473), (72, 177, 494), (72, 177, 257), 
            (72, 177, 263), (72, 177, 312), (72, 244, 401), (72, 244, 320), (72, 244, 401), (72, 244, 388), (72, 244, 473)] 

K = len(alposibles)*len(dposibles)
K

In [ ]:
#Generación de datos aleatoria

alposibles = [(a,b,c) for a in np.random.rand(5) for b in np.random.rand(2) for c in np.random.rand(5)]
dposibles = [(a,b,c) for a in np.random.randint(0, high=100, size=2, dtype='l') 
             for b in np.random.randint(50, high=250, size=2, dtype='l') 
             for c in np.random.randint(250, high=500, size=5, dtype='l')]
K = len(alposibles)*len(dposibles)
K

In [ ]:
def LshapedMulticorte():
    r=0; v=0;
    E = [np.array([[]])] * K
    D = np.array([[]])
    x = np.zeros(c.size)
    theta = 0
    while( True ):
        v += 1
        (xv,thetav) = problemaMaestro( E )
        #CONDICIÓN DE PARADA
        if np.all(x == xv) and np.all(theta == thetav):
            print('-------------------Número de iteraciones\n',v,'\n')
            
            print('-------------------------------Respuesta\n',xv,'\n')
            
            return(xv)
            break
        x = xv; theta = thetav
        k = 0
        
        #Itero sobre todas las posibles realizaciones de \zeta:
        for (al1,al2,al3) in alposibles:
            Tact = np.zeros((12,3)) 
            for i in range(0,3):
                Tact[i,i] = -al1; Tact[i+3,i] = -al2; Tact[i+6,i] = -al3
            for (d1,d2,d3) in dposibles :
                hact = np.append(np.zeros(9),np.array([d1,d2,d3]))
                bact = hact - (Tact @ xv)
                model = gp.Model('Aux')
                vary = model.addVars(range(0,q.size), lb = 0, vtype = GRB.CONTINUOUS)

                model.modelSense = GRB.MINIMIZE
                model.setObjective( quicksum(q[a]*vary[a] for a in range(0,q.size) ) )
                model.addMConstr (W, x = None, sense='=', b = bact )

                model.optimize()
                piact = model.pi
                
                if( thetav[k] < 1/K * np.dot(piact,bact) ):
                    E_s = 1/K*(piact@Tact)
                    e_s = 1/K*np.dot(piact,hact) 
                    if E[k].any() == False:
                        E[k] = np.array([np.hstack( (E_s, e_s) )])
                    else:
                        E[k] = np.vstack( (E[k], np.hstack( (E_s, e_s) )) )

                k+=1     
    return(xv)

In [ ]:
def problemaMaestro(E):    
    model = gp.Model('Maestro')
    varx = model.addVars( range(0,c.size), lb = 50, ub = 1000000, vtype = GRB.CONTINUOUS )
    model.modelSense = GRB.MINIMIZE
    #La siguiente variable cuenta el número de k, tal que s_k es diferente de 0.
    indicesNoVacios = np.count_nonzero([ E[i].any()==True for i in range(0,K)])
    
    if indicesNoVacios == 0:
        model.setObjective( quicksum(varx[a]*c[a] for a in range(0,c.size)) )
    else:
        theta = model.addVars(range(0,indicesNoVacios), lb = float('-Inf'), vtype = GRB.CONTINUOUS)
        model.setObjective( quicksum(varx[a]*c[a] for a in range(0,c.size)) + 
                            quicksum(theta[a] for a in range(0,indicesNoVacios) ) )
        
    lista = np.array([varx[i] for i in range(0,c.size)])
    j = 0
    if  indicesNoVacios > 0: 
        for index in range(0,K):
            if E[index].any() == True:
                etemp = E[index][:,-1]; 
                Etemp = np.hstack((E[index][:,:-1], np.ones((E[index].shape[0],1))))
                l = np.hstack((lista,theta[j]))
                model.addMConstr(Etemp, x = l.tolist(), sense='>=', b = etemp) 
                j+=1
    model.optimize()
    rta = np.array([varx[i].x for i in range(0,c.size)])
    th = np.full(K,float('-Inf'))
    if indicesNoVacios != 0:
        for index in range(0,indicesNoVacios):
            th[index] = theta[index].x
    return (rta,th)

In [ ]:
start = timer()
LshapedMulticorte()
end = timer()
print('\nTiempo:',end - start)


# Cota superior para $cT \hat{x}+D(\hat{x})$ con $100(1-\alpha)\%$ de confianza.
Primero generamos una muestra i.i.d de tamaño N = 5000


In [8]:
#Generación de datos aleatoria

alp = [(a,b,c) for a in np.random.rand(5) for b in np.random.rand(3) for c in np.random.rand(5)]
dp = [(a,b,c) for a in np.random.randint(0, high=100, size=2, dtype='l') 
             for b in np.random.randint(50, high=250, size=4, dtype='l') 
             for c in np.random.randint(250, high=500, size=5, dtype='l')]
N = len(alp)*len(dp)
print(N)
xhat = np.array([ 50,75,209]) 

3000


# Calculamos $\hat{D}_N(\hat{x}) : = \frac{1}{N} \sum_{i=1}^N Q(\hat{x},\zeta)$

In [21]:
def calculocotaSup(x):
    lista = np.array([]) 
    k=0
    #Iteramos sobre las 3000 realizaciones.
    for (al1,al2,al3) in alp:
        Tact = np.zeros((12,3)) 
        for i in range(0,3):
            Tact[i,i] = -al1; Tact[i+3,i] = -al2; Tact[i+6,i] = -al3
        for (d1,d2,d3) in dp :
            print('\n',k,'\n')
            hact = np.append(np.zeros(9),np.array([d1,d2,d3]))
            bact = hact - (Tact @ xhat)
            model = gp.Model('Aux')
            vary = model.addVars(range(0,q.size), lb = 0, vtype = GRB.CONTINUOUS)

            model.modelSense = GRB.MINIMIZE
            model.setObjective( quicksum(q[a]*vary[a] for a in range(0,q.size) ) )
            model.addMConstr (W, x = None, sense='=', b = bact )

            model.optimize()
            lista = np.append(lista, model.objVal)
            k+=1
            
    DN = statistics.mean(lista)
    sd = statistics.stdev( lista, DN )
    sigmaN = statistics.variance(lista) 

    cotaSup = np.dot(c,xhat) + DN + (stats.norm.ppf(1-0.001)*sd/np.sqrt(N))

    
    return np.array([DN,sigmaN,sd])

m = calculocotaSup(xhat)
print(m)


 0 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x084f07e8
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.03s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.7030000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.04 seconds
Optimal objective  3.703000000e+03

 1 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x93d82f93
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3


Solved in 0 iterations and 0.02 seconds
Optimal objective  4.256000000e+03

 12 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x922c481f
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.2620000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  3.262000000e+03

 13 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xbd02f640
Coeffici

       0    3.8990000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  3.899000000e+03

 24 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x600f555d
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    4.2560000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  4.256000000e+03

 25 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 2

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.8920000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.04 seconds
Optimal objective  3.892000000e+03

 36 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x1f3d6b8f
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    4.5329486e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  4.532948625e+03

 37 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical pr

Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.6610000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  3.661000000e+03

 48 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x00b5a6dc
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [8e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.00s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.7590000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  3.759000000e+03

 49 

Gurobi Optimizer version 9.1.2 build v9

...

Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    8.9342891e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  8.934289127e+03

 2950 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x2ed17e63
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    8.8142891e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  8.814289127e+03

 2951 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
T

  RHS range        [2e+00, 5e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    7.6243649e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  7.624364909e+03

 2962 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x434de2c9
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.2200000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optim

  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.5343649e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.534364909e+03

 2974 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xd836983c
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0

Model fingerprint: 0x69d0c495
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    7.8026729e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  7.802672891e+03

 2986 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xaad36d66
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objec

Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xc8fefd34
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.0940000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  3.094000000e+03

 2998 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xca3b9dd0
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s

In [12]:
print('\n---------\nalp=',alp)
print('\n---------\ndp=',dp)


---------
alp= [(0.9408662179114028, 0.5344715065169033, 0.7225584606422026), (0.9408662179114028, 0.5344715065169033, 0.2913801291845928), (0.9408662179114028, 0.5344715065169033, 0.20844494381865597), (0.9408662179114028, 0.5344715065169033, 0.4740016349673879), (0.9408662179114028, 0.5344715065169033, 0.24712336796248757), (0.9408662179114028, 0.23682981639411627, 0.9444580373465088), (0.9408662179114028, 0.23682981639411627, 0.2747266219290154), (0.9408662179114028, 0.23682981639411627, 0.23490245687278188), (0.9408662179114028, 0.23682981639411627, 0.5915797071964715), (0.9408662179114028, 0.23682981639411627, 0.7007477238212008), (0.9408662179114028, 0.5179977258356221, 0.5073226394618291), (0.9408662179114028, 0.5179977258356221, 0.1541621620252719), (0.9408662179114028, 0.5179977258356221, 0.13557720875790813), (0.9408662179114028, 0.5179977258356221, 0.050987517187985665), (0.9408662179114028, 0.5179977258356221, 0.5064355303830672), (0.2868087292039272, 0.9582204887903772, 0

### Los valores encontrados fueron
$$D_N(\hat{x}) =  8567.917736652616 .$$
$$\sigma^2_N(\hat{x}) =  12391469.761976024.$$
$$sd =  3520.151951546414.$$

In [22]:
DN= 7.07625099e+03  
Sigma= 9.26789888e+06
StandardD= 3.04432240e+03


cotaSup = np.dot(c,xhat) + DN + (stats.norm.ppf(1-0.001)*StandardD/np.sqrt(N))

print(cotaSup)

13053.010639150138


In [17]:
DN= 8567.917
Sigma= 12391469.76
StandardD= 3520.15

cotaSup = np.dot(c,xhat) + DN + (stats.norm.ppf(1-0.001)*StandardD/np.sqrt(N))

print(cotaSup)

14571.52268281331


### Genere M = 100 muestras i.i.d de de tamaño n = 1000

In [12]:
index=0
fi = np.zeros(100)
while(index<100):
    alp = [(a,b,c) for a in np.random.rand(5) for b in np.random.rand(2) for c in np.random.rand(5)]
    dp = [(a,b,c) for a in np.random.randint(0, high=100, size=2, dtype='l') 
                 for b in np.random.randint(50, high=250, size=2, dtype='l') 
                 for c in np.random.randint(250, high=500, size=5, dtype='l')]
    listai = np.array([]) 
    k=0
    #Iteramos sobre las realizaciones.
    for (al1,al2,al3) in alp:
        Tact = np.zeros((12,3)) 
        for i in range(0,3):
            Tact[i,i] = -al1; Tact[i+3,i] = -al2; Tact[i+6,i] = -al3
        for (d1,d2,d3) in dp :
            print('\n',(index,k),'\n')
            hact = np.append(np.zeros(9),np.array([d1,d2,d3]))
            bact = hact - (Tact @ xhat)
            model = gp.Model('Aux')
            vary = model.addVars(range(0,q.size), lb = 0, vtype = GRB.CONTINUOUS)

            model.modelSense = GRB.MINIMIZE
            model.setObjective( quicksum(q[a]*vary[a] for a in range(0,q.size) ) )
            model.addMConstr (W, x = None, sense='=', b = bact )

            model.optimize()
            listai = np.append(listai, model.objVal)
            k+=1
    fi[index] = np.min(listai) + np.dot(c,xhat) #Valor óptimo del i-ésimo problema
    index+=1

media = statistics.mean(fi)
varianza = statistics.variance(fi)
desvestandar = statistics.stdev(fi)
cotaInf = media - (stats.norm.ppf(1-0.001)*desvestandar/np.sqrt(100))



 (0, 0) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x665bbf1e
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+01, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.7396895e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  3.739689506e+03

 (0, 1) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x182822dc
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range 


Solved in 0 iterations and 0.02 seconds
Optimal objective  3.913000000e+03

 (0, 12) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x4a8931f1
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+01, 5e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.6989348e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.698934758e+03

 (0, 13) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xabb870c

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.4989848e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  3.498984776e+03

 (0, 24) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x1697555e
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+01, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.4985690e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.498569018e+03

 (0, 25) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 

  RHS range        [2e+01, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.8829848e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.882984776e+03

 (0, 36) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x66b4ab89
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+01, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    6.2749848e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Op

Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [7e+00, 5e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.1853175e+04   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  1.185317506e+04

 (0, 48) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x44ce4c87
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [7e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    D

...


 (19, 658) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xf3884ffe
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.5735547e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.573554710e+03

 (19, 659) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xd8f64259
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective 

       0    5.9342041e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  5.934204132e+03

 (19, 670) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xc4dd333e
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.0838828e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.083882845e+03

 (19, 671) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model w

Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    8.6433585e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  8.643358544e+03

 (19, 682) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x1d0ebf4f
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    7.1133585e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.02 seconds
Optimal objective  7.113358544e+03

Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e+00, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.0131359e+04   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  1.013135854e+04

 (19, 694) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x30f34a65
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e+00, 3e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.   

Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0xcddcb17d
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+01, 4e+02]
Presolve removed 12 rows and 21 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.0788000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  5.078800031e+03

 (19, 706) 

Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 2 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 12 rows, 21 columns and 30 nonzeros
Model fingerprint: 0x88f54720
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 3e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range  

In [ ]:
print(fi)

In [5]:
np.dot(c,xhat)

5805

In [6]:
fiiii = [8934, 8416, 8927, 8311, 8318, 9186, 8696, 8794, 8710, 8899, 8962, 8479, 
 8696, 8563, 9053, 8759, 8605, 8479, 8738, 8857, 8297, 8654, 9249, 8521, 8892, 8906, 8479, 8878, 9389, 8227,
 8493, 9207, 8794, 8192, 8430, 8353, 8738, 9235, 8668, 8850, 8808, 8710, 8360, 8892, 8619, 8500, 8507, 9053,
 8696, 9095, 8885, 8934, 8416, 8927, 8311, 8318, 9186, 8696, 8794, 8710, 8899, 8962, 8479, 
 8696, 8563, 9053, 8759, 8605, 8479, 8738, 8857, 8297, 8654, 9249, 8521, 8892, 8906, 8479, 8878, 9389, 8227,
 8493, 9207, 8794, 8192, 8430, 8353, 8738, 9235, 8668, 8850, 8808, 8710, 8360, 8892, 8619, 8500, 8507, 9053,
 8696]
len(fiiii)

media = statistics.mean(fiiii)
varianza = statistics.variance(fiiii)
desvestandar = statistics.stdev(fiiii)
print((stats.norm.ppf(1-0.001)*desvestandar/np.sqrt(100)))
cotaInf = media - (stats.norm.ppf(1-0.001)*desvestandar/np.sqrt(100))

print('\n Media:', media, '\n')

print('\n Varianza:', varianza, '\n')

print('\n Desviación estándar:', desvestandar, '\n')

print('\n Cota inferior:', cotaInf, '\n')

stats.norm.ppf(1-0.001)

87.77724487085688

 Media: 8719.38 


 Varianza: 80682.92484848485 


 Desviación estándar: 284.04739894687447 


 Cota inferior: 8631.602755129143 



3.090232306167813